In [1]:
# import library
import tensorflow as tf
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import csv
import xlsxwriter

import pythainlp
import pythaispell
from gingerit.gingerit import GingerIt
from langdetect import detect
import nltk
from keras import *
from keras.utils import to_categorical
from pythainlp import word_tokenize
from pythainlp.corpus import thai_stopwords
from pythainlp.corpus import wordnet
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import confusion_matrix, classification_report
from pythainlp.corpus.common import thai_words
from pythainlp.tokenize import dict_trie
from pythainlp.tag.named_entity import ThaiNameTagger
from pythainlp.word_vector import get_model
from sklearn.model_selection import train_test_split

from sklearn.model_selection import train_test_split

Using TensorFlow backend.


In [2]:
# import data from Excel
df = pd.read_excel('./Data/All_Perfect_Data.xlsx',sheet_name=None)

In [3]:
df

OrderedDict([('Sheet0',
                    a  Category                                        Description
              0     0         0  SmartphonesSAMSUNG Galaxy A20s *ประกันศูนย์ 1ป...
              1     1         0  SmartphonesSamsung A30 Ram4/64GB (เครื่องศูนย์...
              2     2         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...
              3     3         0  SmartphonesSamsung Galaxy M30s (4/64GB) ( โทรศ...
              4     4         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...
              ..   ..       ...                                                ...
              821  75         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              822  76         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              823  77         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              824  78         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              825  79         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่อ

In [4]:
df0 = df['Sheet0']
df0.head()

a  Category                                        Description
0  0         0  SmartphonesSAMSUNG Galaxy A20s *ประกันศูนย์ 1ป...
1  1         0  SmartphonesSamsung A30 Ram4/64GB (เครื่องศูนย์...
2  2         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...
3  3         0  SmartphonesSamsung Galaxy M30s (4/64GB) ( โทรศ...
4  4         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...

In [5]:
df0.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 826 entries, 0 to 825
Data columns (total 3 columns):
a              826 non-null int64
Category       826 non-null int64
Description    826 non-null object
dtypes: int64(2), object(1)
memory usage: 19.5+ KB


# Process text

In [27]:
import re
import string

# word correction for EN
#parser = GingerIt()

# download stopwords of TH and EN
nltk.download('words')
th_stop = tuple(thai_stopwords())
en_stop = tuple(get_stop_words('en'))
p_stemmer = PorterStemmer()

# clean the text
def clean_text(msg): 
    
    # ลบ text ที่อยู่ใน []
    #msg = re.sub(r'[<*●•►【】✨✈✅#?>]','', str(msg))
    #msg = re.sub(r'✅','',msg)
    # ลบ hashtag
    #msg = re.sub(r'#','',msg)

    msg = re.sub(r"[^A-Za-z0-9ก-๙\.\s]","", str(msg))
    msg = re.sub(r"SKU\s\d+TH\d+"," ",str(msg))
    msg = re.sub(r"[A-Za-z]{30,}"," ",str(msg))
    
    # Delete punctuation
    str_punc = string.punctuation.replace(".","")
    for c in str_punc:
        msg = re.sub(r'\{}'.format(c),'',str(msg))
    
    
    # ลบ separator เช่น \n \t
    msg = ' '.join(msg.split())
    
    return msg

# split to words from text
def split_word(text):
    words = word_tokenize(text,engine='newmm',keep_whitespace=False)

    # Remove stop words TH and EN
    words = [i for i in words if not i in th_stop and not i in en_stop]
    
    # รากศัพท์
    # EN
    #words = [p_stemmer.stem(i) for i in words]
    
    # TH
    #tokens_temp=[]
    #for i in words:
    #    w_syn = wordnet.synsets(i)
    #    if (len(w_syn)>0) and (len(w_syn[0].lemma_names('tha'))>0) and not (w_syn[0].lemma_names('tha')[0].isdigit()):
    #        tokens_temp.append(w_syn[0].lemma_names('tha')[0])
    #    else:
     #       tokens_temp.append(i)
    
    #words = tokens_temp

    return words

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\super\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


In [28]:
des = df0['Description'].values
des[0:2]

array(['SmartphonesSAMSUNG Galaxy A20s *ประกันศูนย์ 1ปี* อุปกรณ์ในกล่อง หัวชาร์จ / สาย USB Type-CA20s ไม่ได้แถม หูฟัง / ฟิล์ม / เคส มาจากทางSAMSUNGทางร้านต้องแกะกล่องสินค้าเพื่อนำใบประกันส่งบริษัทผู้ผลิต****************************************แบรนด์ ซัมซุงSKU 568380632_TH-1042940038ประเภทของการรับประกัน มีการรับประกันกล้องหน้า (เมกะพิกเซล) 7 MP ขึ้นไปModel samsung galaxy A20sกล้องด้านหลัง 11-15MPระยะเวลาการรับประกัน 1 ปีBattery Capacity 4000 - 4999 mAh',
       'SmartphonesSamsung A30 Ram4/64GB (เครื่องศูนย์ไทย,มีประกันศูนย์1ปี)สมาร์ทโฟน (โทรศัพท์มือถือพร้อมระบบปฏิบัติการ)จอแสดงผล Super AMOLED 24-bit (16 ล้านสี)- หน้าจอทรงหยดน้ำ รูปตัว U (Infinity U)- ระบบสัมผัส Multi-Touch- กว้าง 6.4 นิ้ว (แนวทะแยง)- ความละเอียด 1080 x 2340 พิกเซล- Capacitiveระบบเซ็นเซอร์ (Sensor)- ระบบตรวจสอบลายนิ้วมือ (Fingerprint)- ระบบจดจำใบหน้า (Face Detection)- ระบบหมุนภาพอัตโนมัติ (Accelerometer)- ระบบเปิด/ปิดหน้าจออัตโนมัติขณะสนทนา (Proximity)ระบบปฏิบัติการ: Android 9.0 (Pie)หน่วยประมวลผล : Exynos 7904 Octa Co

In [29]:
des_clean = [clean_text(txt) for txt in des]
des_clean[0:3]

['SmartphonesSAMSUNG Galaxy A20s ประกันศูนย์ 1ปี อุปกรณ์ในกล่อง หัวชาร์จ สาย USB TypeCA20s ไม่ได้แถม หูฟัง ฟิล์ม เคส มาจากทางSAMSUNGทางร้านต้องแกะกล่องสินค้าเพื่อนำใบประกันส่งบริษัทผู้ผลิตแบรนด์ ซัมซุง ประเภทของการรับประกัน มีการรับประกันกล้องหน้า เมกะพิกเซล 7 MP ขึ้นไปModel samsung galaxy A20sกล้องด้านหลัง 1115MPระยะเวลาการรับประกัน 1 ปีBattery Capacity 4000 4999 mAh',
 'SmartphonesSamsung A30 Ram464GB เครื่องศูนย์ไทยมีประกันศูนย์1ปีสมาร์ทโฟน โทรศัพท์มือถือพร้อมระบบปฏิบัติการจอแสดงผล Super AMOLED 24bit 16 ล้านสี หน้าจอทรงหยดน้ำ รูปตัว U Infinity U ระบบสัมผัส MultiTouch กว้าง 6.4 นิ้ว แนวทะแยง ความละเอียด 1080 x 2340 พิกเซล Capacitiveระบบเซ็นเซอร์ Sensor ระบบตรวจสอบลายนิ้วมือ Fingerprint ระบบจดจำใบหน้า Face Detection ระบบหมุนภาพอัตโนมัติ Accelerometer ระบบเปิดปิดหน้าจออัตโนมัติขณะสนทนา Proximityระบบปฏิบัติการ Android 9.0 Pieหน่วยประมวลผล Exynos 7904 Octa Core ความเร็ว 1.8 GHzหน่วยความจำ3264 GB ตัวเครื่อง RAM 34GBการ์ดหน่วยความจำ microSD สูงสุด 512 GBกล้องดิจิตอล 16 5 ล้านพิกเซล Dual Ca

In [30]:
len(des_clean)

826

In [31]:
des_token = [split_word(txt) for txt in des_clean]
des_token

[['SmartphonesSAMSUNG',
  'Galaxy',
  'A',
  '20',
  's',
  'ประกัน',
  'ศูนย์',
  '1',
  'ปี',
  'อุปกรณ์',
  'กล่อง',
  'หัว',
  'ชาร์จ',
  'สาย',
  'USB',
  'TypeCA',
  '20',
  's',
  'แถม',
  'หูฟัง',
  'ฟิล์ม',
  'เคส',
  'มาจาก',
  'SAMSUNG',
  'ร้าน',
  'แกะ',
  'กล่อง',
  'สินค้า',
  'ใบ',
  'ประกัน',
  'บริษัทผู้ผลิต',
  'แบรนด์',
  'ซัมซุง',
  'ประเภท',
  'การรับประกัน',
  'การรับประกัน',
  'กล้อง',
  'หน้า',
  'เมกะ',
  'พิกเซล',
  '7',
  'MP',
  'ขึ้นไป',
  'Model',
  'samsung',
  'galaxy',
  'A',
  '20',
  's',
  'กล้อง',
  'ด้านหลัง',
  '1115',
  'MP',
  'ระยะเวลา',
  'การรับประกัน',
  '1',
  'ปี',
  'Battery',
  'Capacity',
  '4000',
  '4999',
  'mAh'],
 ['SmartphonesSamsung',
  'A',
  '30',
  'Ram',
  '464',
  'GB',
  'เครื่อง',
  'ศูนย์',
  'ไทย',
  'ประกัน',
  'ศูนย์',
  '1',
  'ปี',
  'สมาร์ท',
  'โฟน',
  'โทรศัพท์มือถือ',
  'ระบบปฏิบัติการ',
  'จอแสดงผล',
  'Super',
  'AMOLED',
  '24',
  'bit',
  '16',
  'ล้าน',
  'สี',
  'หน้าจอ',
  'หยดน้ำ',
  'รูป',
  'ตัว',
  'U

In [32]:
from pythainlp.tag import pos_tag

pos_token = []
for i,d in enumerate(des_token):
    tag = pos_tag([txt for txt in d], corpus='orchid')
    pos_token.append(tag)
    

In [33]:
pos_token

[[('SmartphonesSAMSUNG', 'NCMN'),
  ('Galaxy', 'NCMN'),
  ('A', 'NCMN'),
  ('20', 'DCNM'),
  ('s', 'NCMN'),
  ('ประกัน', 'VSTA'),
  ('ศูนย์', 'DCNM'),
  ('1', 'DCNM'),
  ('ปี', 'CMTR'),
  ('อุปกรณ์', 'NCMN'),
  ('กล่อง', 'VACT'),
  ('หัว', 'NCMN'),
  ('ชาร์จ', 'NCMN'),
  ('สาย', 'NCMN'),
  ('USB', 'NCMN'),
  ('TypeCA', 'NCMN'),
  ('20', 'DCNM'),
  ('s', 'NCMN'),
  ('แถม', 'CNIT'),
  ('หูฟัง', 'NCMN'),
  ('ฟิล์ม', 'NCMN'),
  ('เคส', 'VATT'),
  ('มาจาก', 'JSBR'),
  ('SAMSUNG', 'NCMN'),
  ('ร้าน', 'NCMN'),
  ('แกะ', 'VACT'),
  ('กล่อง', 'NCMN'),
  ('สินค้า', 'NCMN'),
  ('ใบ', 'VSTA'),
  ('ประกัน', 'ADVN'),
  ('บริษัทผู้ผลิต', 'NCMN'),
  ('แบรนด์', 'NCMN'),
  ('ซัมซุง', 'NCMN'),
  ('ประเภท', 'CLTV'),
  ('การรับประกัน', 'ADVN'),
  ('การรับประกัน', 'ADVN'),
  ('กล้อง', 'NCMN'),
  ('หน้า', 'VATT'),
  ('เมกะ', 'NCMN'),
  ('พิกเซล', 'NCMN'),
  ('7', 'NCNM'),
  ('MP', 'NCMN'),
  ('ขึ้นไป', 'CNIT'),
  ('Model', 'NCMN'),
  ('samsung', 'NCMN'),
  ('galaxy', 'NCMN'),
  ('A', 'NCMN'),
  ('20', 'DCNM'

In [34]:
# convert list of tuples to dataframe

list_df = []
for i,l in enumerate(pos_token):
    df = pd.DataFrame(l, columns=['word', 'pos'])
    df.insert(0,'idx',i)
    list_df.append(df)

data_for_excel = pd.concat(list_df,ignore_index=True)

In [35]:
data_for_excel

idx                word   pos
0         0  SmartphonesSAMSUNG  NCMN
1         0              Galaxy  NCMN
2         0                   A  NCMN
3         0                  20  DCNM
4         0                   s  NCMN
...     ...                 ...   ...
107335  825                 553  DCNM
107336  825            ระยะเวลา  NCMN
107337  825        การรับประกัน  ADVN
107338  825                   2  DCNM
107339  825                  ปี  CMTR

[107340 rows x 3 columns]

In [36]:
data_for_excel.to_excel('./Data/Sheet0_token.xlsx',engine='xlsxwriter')